# Recommandation collaborative : genres, notes et hybride

In [9]:
import pandas as pd
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import warnings
warnings.filterwarnings('ignore')

In [ ]:
all = pd.read_csv(r"C:\Users\nolle\OneDrive\Documents\Université\M2\Mémoire\Base de données traitées\All.csv")

## I. Création des matrices de similarité

In [ ]:
ratings_matrix = all.pivot_table(index='userId', columns='title_clean_x', values='rating')

In [ ]:
df_exploded = all.copy()
df_exploded['genres_x_x'] = df_exploded['genres_x_x'].str.split('|')
df_exploded = df_exploded.explode('genres_x_x')
df_exploded = df_exploded.rename(columns={'genres_x_x': 'Genre'})

In [13]:
df_exploded

userId  movieId  rating  timestamp        Genre  \
0            1     1193       5  978300760        Drama   
1            2     1193       5  978298413        Drama   
2           12     1193       4  978220179        Drama   
3           15     1193       4  978199279        Drama   
4           17     1193       5  978158471        Drama   
...        ...      ...     ...        ...          ...   
898685    5949     2198       5  958846401  Documentary   
898686    5675     2703       3  976029116        Drama   
898687    5851     3607       5  957756608       Comedy   
898687    5851     3607       5  957756608        Drama   
898687    5851     3607       5  957756608      Western   

                            title_bis_x  \
0       One Flew Over the Cuckoo's Nest   
1       One Flew Over the Cuckoo's Nest   
2       One Flew Over the Cuckoo's Nest   
3       One Flew Over the Cuckoo's Nest   
4       One Flew Over the Cuckoo's Nest   
...                                 ...   
898685                      Modulations   
898686                   Broken Vessels   
898687                One Little Indian   
898687                One Little Indian   
898687                One Little Indian   

                                 title_clean_x  date_x  budget_x  \
0       One Flew Over the Cuckoo's Nest (1975)    1975   3000000   
1       One Flew Over the Cuckoo's Nest (1975)    1975   3000000   
2       One Flew Over the Cuckoo's Nest (1975)    1975   3000000   
3       One Flew Over the Cuckoo's Nest (1975)    1975   3000000   
4       One Flew Over the Cuckoo's Nest (1975)    1975   3000000   
...                                        ...     ...       ...   
898685                      Modulations (1998)    1998         0   
898686                   Broken Vessels (1998)    1998         0   
898687                One Little Indian (1973)    1973         0   
898687                One Little Indian (1973)    1973         0   
898687                One Little Indian (1973)    1973         0   

                                               overview_x  ...  \
0       While serving time for insanity at a state men...  ...   
1       While serving time for insanity at a state men...  ...   
2       While serving time for insanity at a state men...  ...   
3       While serving time for insanity at a state men...  ...   
4       While serving time for insanity at a state men...  ...   
...                                                   ...  ...   
898685  Less a documentary than a primer on all electr...  ...   
898686  A young Pennsylvania man moves to Los Angeles ...  ...   
898687  An Army deserter (James Garner) flees by camel...  ...   
898687  An Army deserter (James Garner) flees by camel...  ...   
898687  An Army deserter (James Garner) flees by camel...  ...   

                                                tagline_x  \
0                 If he's crazy, what does that make you?   
1                 If he's crazy, what does that make you?   
2                 If he's crazy, what does that make you?   
3                 If he's crazy, what does that make you?   
4                 If he's crazy, what does that make you?   
...                                                   ...   
898685                                 Cinema for the Ear   
898686                  Over the edge and out of control.   
898687  A boy turned Indian, a trooper turned deserter...   
898687  A boy turned Indian, a trooper turned deserter...   
898687  A boy turned Indian, a trooper turned deserter...   

                  genres_x_y                      title_bis_y  \
0                      Drama  One Flew Over the Cuckoo's Nest   
1                      Drama  One Flew Over the Cuckoo's Nest   
2                      Drama  One Flew Over the Cuckoo's Nest   
3                      Drama  One Flew Over the Cuckoo's Nest   
4                      Drama  One Flew Over the Cuckoo's Nest   
...                      ...                     

In [14]:
genre_profiles = pd.pivot_table(
    df_exploded,
    index='userId',           # en lignes
    columns='Genre',     # en colonnes
    values='rating',          # valeurs à agréger
    aggfunc='mean'            # fonction d'agrégation
).fillna(0)                   # pour remplacer les NaN

In [15]:
genre_profiles.loc[1].sort_values(ascending = False)

Genre
War            5.000000
Sci-Fi         4.500000
Drama          4.428571
Action         4.333333
Musical        4.285714
Children's     4.250000
Animation      4.176471
Comedy         4.142857
Crime          4.000000
Fantasy        4.000000
Adventure      4.000000
Thriller       3.666667
Romance        3.600000
Film-Noir      0.000000
Mystery        0.000000
Horror         0.000000
Documentary    0.000000
Western        0.000000
Name: 1, dtype: float64

Pour un utilisateur, on prend la somme de la moyenne de chaque genre puis on regarde la proportion de chaque genre dans cette note avec le code ci-dessous. 

In [16]:
# La fonction div divise chaque cellule du DataFrame par la somme de la ligne

genre_profiles = genre_profiles.div(genre_profiles.sum(axis=1), 
                                    axis = 0).fillna(0)

In [17]:
genre_profiles

Genre     Action  Adventure  Animation  Children's    Comedy     Crime  \
userId                                                                   
1       0.079681   0.073552   0.076796    0.078149  0.076178  0.073552   
2       0.069491   0.072811   0.000000    0.000000  0.069875  0.071539   
3       0.081067   0.081956   0.079957    0.079957  0.076387  0.000000   
4       0.101189   0.104048   0.000000    0.096044  0.000000  0.000000   
5       0.043134   0.049604   0.086267    0.069014  0.059262  0.061465   
...          ...        ...        ...         ...       ...       ...   
6036    0.047403   0.048115   0.063779    0.056659  0.051663  0.056718   
6037    0.053388   0.056161   0.058241    0.053388  0.051923  0.055672   
6038    0.070796   0.000000   0.176991    0.106195  0.141593  0.000000   
6039    0.054451   0.058340   0.054199    0.053383  0.055546  0.060501   
6040    0.043350   0.042735   0.053182    0.060779  0.048520  0.060779   

Genre   Documentary     Drama   Fantasy  Film-Noir    Horror   Musical  \
userId                                                                   
1          0.000000  0.081432  0.073552   0.000000  0.000000  0.078805   
2          0.000000  0.077122  0.059893   0.079857  0.059893  0.000000   
3          0.000000  0.079957  0.000000   0.000000  0.069962  0.079957   
4          0.000000  0.110450  0.096044   0.000000  0.104048  0.000000   
5          0.060387  0.053261  0.000000   0.069014  0.051760  0.057511   
...             ...       ...       ...        ...       ...       ...   
6036       0.065673  0.057257  0.047323   0.067862  0.048994  0.060396   
6037       0.058241  0.057134  0.058241   0.050152  0.059859  0.058241   
6038       0.000000  0.132743  0.000000   0.000000  0.088496  0.000000   
6039       0.000000  0.059871  0.049157   0.066551  0.060501  0.055459   
6040       0.069896  0.057321  0.051662   0.065844  0.037625  0.058880   

Genre    Mystery   Romance    Sci-Fi  Thriller       War   Western  
userId                                                              
1       0.000000  0.066196  0.082746  0.067422  0.091939  0.000000  
2       0.066548  0.073505  0.069875  0.069875  0.073203  0.086512  
3       0.059968  0.074960  0.066631  0.075959  0.000000  0.093283  
4       0.000000  0.000000  0.088040  0.084038  0.120055  0.096044  
5       0.054225  0.052510  0.052993  0.050192  0.060387  0.069014  
...          ...       ...       ...       ...       ...       ...  
6036    0.055081  0.054938  0.045544  0.051428  0.061810  0.059358  
6037    0.054601  0.053873  0.053829  0.054209  0.058241  0.054601  
6038    0.000000  0.141593  0.000000  0.000000  0.141593  0.000000  
6039    0.063170  0.057140  0.060501  0.062662  0.060501  0.068064  
6040    0.067686  0.052976  0.052396  0.059610  0.055981  0.060779  

[6040 rows x 18 columns]

In [20]:
genre_profiles_pearson = genre_profiles.T.corr().fillna(0)

In [26]:
genre_profiles.sum(axis = 1)

userId
1       1.0
2       1.0
3       1.0
4       1.0
5       1.0
       ... 
6036    1.0
6037    1.0
6038    1.0
6039    1.0
6040    1.0
Length: 6040, dtype: float64

- df_exploded contient pour un film autant de lignes que de genres qu'il possède. Par exemple, si Toy Story possède 3 genres il apparaîtra 3 fois pour chaque user ayant noté ce film.
- genre_profiles contient la préférence en proportion de chaque utilisateur de tel genre de film et remplace les trous par des 0

In [27]:
similarity_genres = pd.DataFrame(
    cosine_similarity(genre_profiles),
    index=genre_profiles.index,
    columns=genre_profiles.index
)

similarity_genres calcule la similarité entre les différents utilisateurs selon les préférences calculées précedemment pour les genres.

In [6]:
pearson_matrix = ratings_matrix.T.corr().fillna(0)

Corrélation de Pearson : mesure statistique de la relation linéaire entre deux vecteurs numériques.
- +1 : corrélation parfaitement positive  
- 0 : aucune corrélation linéaire   
- –1 : corrélation parfaitement négative  

In [10]:
pearson_matrix

userId          1             2         3             4         5     \
userId                                                                 
1       1.000000e+00  4.166667e-01 -0.279508  1.000000e+00 -0.103807   
2       4.166667e-01  1.000000e+00  0.229416 -5.102800e-16 -0.214724   
3      -2.795085e-01  2.294157e-01  1.000000  1.000000e+00 -0.437621   
4       1.000000e+00 -5.102800e-16  1.000000  1.000000e+00 -1.000000   
5      -1.038068e-01 -2.147244e-01 -0.437621 -1.000000e+00  1.000000   
...              ...           ...       ...           ...       ...   
6036   -1.450534e-01  3.701641e-01  0.195633  6.191057e-01  0.182831   
6037   -4.037864e-01  3.104790e-01 -0.307860 -1.000000e+00 -0.106543   
6038    0.000000e+00  0.000000e+00  0.000000  0.000000e+00 -1.000000   
6039    9.335201e-02  6.437963e-01  0.086711  0.000000e+00  1.000000   
6040   -5.768888e-16  4.317839e-03 -0.569516  7.254763e-02  0.370456   

userId      6         7         8         9         10    ...      6031  \
userId                                                    ...             
1       0.219956  0.000000 -0.500000  0.297020 -0.006330  ... -0.160128   
2      -0.057486  0.118918  0.034021  0.303790 -0.124092  ... -0.764706   
3      -0.342997  0.875000 -0.525226  0.037662 -0.028417  ... -0.555556   
4       0.000000  0.866025  0.500000  1.000000  0.000000  ... -0.577350   
5      -0.592014 -0.028516  0.227073  0.012665 -0.018543  ...  0.261429   
...          ...       ...       ...       ...       ...  ...       ...   
6036   -0.322995  0.341482  0.312371  0.097165  0.032007  ...  0.034980   
6037   -0.266872 -0.095433 -0.082988  0.214035 -0.038761  ... -0.009517   
6038    0.000000  0.000000  0.000000  1.000000  0.750568  ... -1.000000   
6039   -0.292770  0.000000  0.000000  0.000000 -0.036995  ... -0.292685   
6040   -0.044118  0.745499  0.409582  0.196512 -0.050063  ... -0.432146   

userId          6032      6033      6034      6035      6036      6037  \
userId                                                                   
1       7.559289e-01  0.000000  0.000000  0.381246 -0.145053 -0.403786   
2       1.277753e-01  0.338761  0.000000  0.356001  0.370164  0.310479   
3      -3.429972e-01 -0.801784  0.000000  0.346451  0.195633 -0.307860   
4      -2.220446e-16 -0.316228  0.000000  0.494535  0.619106 -1.000000   
5       8.660254e-01  0.404095  1.000000  0.542045  0.182831 -0.106543   
...              ...       ...       ...       ...       ...       ...   
6036    2.203954e-01  0.281960  0.224733  0.343412  1.000000  0.178163   
6037    2.520584e-01 -0.086146  0.165395  0.301064  0.178163  1.000000   
6038    1.324532e-01  0.000000  0.000000  1.000000 -0.181444  0.000000   
6039    6.017876e-03  0.000000  0.577350  0.158114  0.142415  0.161999   
6040    3.944508e-01  0.052414 -0.538816  0.156453  0.397822  0.210387   

userId      6038      6039          6040  
userId                                    
1       0.000000  0.093352 -5.768888e-16  
2       0.000000  0.643796  4.317839e-03  
3       0.000000  0.086711 -5.695161e-01  
4       0.000000  0.000000  7.254763e-02  
5      -1.000000  1.000000  3.704555e-01  
...          ...       ...           ...  
6036   -0.181444  0.142415  3.978225e-01  
6037    0.000000  0.161999  2.103867e-01  
6038    1.000000  0.559017 -3.457522e-01  
6039    0.559017  1.000000  3.328898e-01  
6040   -0.345752  0.332890  1.000000e+00  

[6040 rows x 6040 columns]

In [19]:
pearson_matrix.loc[1].sort_values(ascending = False).sample(5)

userId
2846   -0.636396
1008   -0.577350
3255    0.000000
3281   -0.211773
3143   -0.055141
Name: 1, dtype: float64

## II. Système de recommandations

In [ ]:
import numpy as np
import pandas as pd

def recommend_top_movies(user_id, all, similarity_matrix, top_n=10):
    # Vérifie si l'utilisateur existe dans la base
    if user_id not in all['userId'].unique():
        raise ValueError(f"User ID {user_id} not found in dataset.")
    
    # Liste des films déjà vus par l'utilisateur
    seen_movies = all[all['userId'] == user_id]['title_clean_x'].tolist()

    # Sélection des 20 utilisateurs les plus similaires (avec similarité > 0)
    similar_users = similarity_matrix.loc[user_id].drop(user_id)
    similar_users = similar_users[similar_users > 0].sort_values(ascending=False).head(20).index

    # On prend les notes des utilisateurs similaires sur les films non vus
    df_neighbors = all[(all['userId'].isin(similar_users)) & (~all['title_clean_x'].isin(seen_movies))]

    if df_neighbors.empty:
        return pd.DataFrame(columns=['title_clean_x', 'predicted_rating'])

    def weighted_average_rating(group):
        weights = []
        ratings = []
        for uid, rating in zip(group['userId'], group['rating']):
            if uid in similarity_matrix.columns:
                sim = similarity_matrix.at[user_id, uid]
                if sim > 0:
                    weights.append(sim)
                    ratings.append(rating)
        if weights:
            return np.average(ratings, weights=weights)
        else:
            return np.nan

    # Calcul des notes prédites pour chaque film non vu
    pred_scores = df_neighbors.groupby('title_clean_x').apply(weighted_average_rating).dropna()

    # Retourne les top N recommandations
    recommendations = pred_scores.sort_values(ascending=False).head(top_n).reset_index()
    recommendations.columns = ['title_clean_x', 'predicted_rating']
    
    return recommendations

In [ ]:
recommend_top_movies(user_id=1, all=all, similarity_matrix=pearson_matrix, top_n=10).set_index("title_clean_x")

predicted_rating
title_clean_x                                    
Breaking the Waves (1996)                     5.0
Half Baked (1998)                             5.0
The Outlaw Josey Wales (1976)                 5.0
High Noon (1952)                              5.0
Henry V (1989)                                5.0
The Manchurian Candidate (1962)               5.0
The Maltese Falcon (1941)                     5.0
Notorious (1946)                              5.0
Conan the Barbarian (1982)                    5.0
Halloween II (1981)                           5.0

## III. Test de la performance du modèle

In [ ]:
from sklearn.metrics import mean_squared_error, mean_absolute_error
import numpy as np

#  Initialisation de la fonction

def evaluate_rmse_mae(all, similarity_matrix, test_fraction = 0.2) :
    users = all['userId'].unique()
    y_true_all = []
    y_pred_all = []

    
    # Ici on définit ce que va faire la fonction qu'on appelera plus tard 

    def weighted_average_rating(group, similarity_matrix, user_id) :
        weights = []
        ratings = []
        for uid, rating in zip(group['userId'], group['rating']) :
            if uid in similarity_matrix.columns :
                w = similarity_matrix.at[user_id, uid]
                if w > 0 :
                    weights.append(w)
                    ratings.append(rating)
        if weights :
            return np.average(ratings, weights = weights)
        else :
            return np.nan  # Ignorer si aucun poids valide

    
    # Maintenant que la fonction est définie, on peut boucler sur les utilisateurs pour faire nos prédictions

    for user_id in users :
        user_data = all[all['userId'] == user_id] 
        if len(user_data) < 5 :
            continue

        test_data = user_data.sample(frac = test_fraction, random_state = 42) # 20% des films pour cet user
        train_data = user_data.drop(test_data.index) # 80 % des autres films pour cet user
        df_train = pd.concat([all[all['userId'] != user_id], train_data], ignore_index = True) # Tous les films sauf les 20% pour cet user

        similar_users = similarity_matrix.loc[user_id].drop(user_id).sort_values(ascending = False).head(20).index
        candidates = df_train[(df_train['userId'].isin(similar_users)) & (df_train['title_clean_x'].isin(test_data['title_clean_x']))]
        # candidates est un df composé des notes de tous les voisins sur les films qui sont présents dans test, le but étant de comparer

        if candidates.empty :
            continue

        
        # Ici on va appliquer à chaque film la fonction qui permet d'avoir la note prédite
        # Ici l'argument 'group' correspond à chaque modalité du groupby soit chaque film
        
        pred_scores = candidates.groupby('title_clean_x').apply(
            lambda group : weighted_average_rating(group, similarity_matrix, user_id)
        ).dropna()

        # pred_scores est une Series avec pour index le 'title_clean_x' et la valeur prédite pour ce film

        for movie_id, pred_rating in pred_scores.items() :
            true_rating = test_data[test_data['title_clean_x'] == movie_id]['rating'].values
            if len(true_rating) > 0 :
                y_true_all.append(true_rating[0])
                y_pred_all.append(pred_rating)

    if len(y_true_all) == 0 :
        return {'RMSE': None, 'MAE': None, 'n_predictions': 0}

    rmse = np.sqrt(mean_squared_error(y_true_all, y_pred_all))
    mae = mean_absolute_error(y_true_all, y_pred_all)

    return {
        'RMSE': round(rmse, 4),
        'MAE': round(mae, 4),
        'n_predictions': len(y_true_all)
    }

In [ ]:
# 1. Erreurs pour le système par GENRE
results_genre_error = evaluate_rmse_mae(all, similarity_genres)
print("Genres -", results_genre_error)

Genres - {'RMSE': 1.0407, 'MAE': 0.8056, 'n_predictions': 161496}


In [ ]:
# 2. Erreurs pour le système par NOTE
results_note_error = evaluate_rmse_mae(all, pearson_matrix)
print("Notes -", results_note_error)

Notes - {'RMSE': 0.9683, 'MAE': 0.6919, 'n_predictions': 40991}


In [ ]:
# 3. Erreurs pour le système HYBRIDE
hybrid_matrix = 0.5 * similarity_genres + 0.5 * pearson_matrix
results_hybrid_error = evaluate_rmse_mae(all, hybrid_matrix)
print("Hybride -", results_hybrid_error)

Hybride - {'RMSE': 0.872, 'MAE': 0.595, 'n_predictions': 49644}
